In [33]:
import os
import pandas as pd

from data_dir import genome_grch37, grch37_sample_dir, genome_grch37_dir
from data_dir import genome_grch38, grch38_sample_dir, genome_grch38_dir

In [51]:
def _parse_desc(desc):
    # desc_obj = {'gene': '', 'gene_id': '', 'genebank': '', 'ensembl': ''}
    desc_obj = {}
    arr = desc.split(';') # Split desc with semicolon as separator.
    for e in arr:
        det = e.split('=') # Split every parameter and its corresponding value.
        param = det[0].lower()
        val = det[1]
        desc_obj[param] = val
        if param == "dbxref":
            # Parse value of dbxref.
            # i.e. Dbxref=GeneID:653635,Genbank:NR_024540.1,HGNC:HGNC:38034
            # param = dbxref (in lowercase)
            # val = GeneID:653635,Genbank:NR_024540.1,HGNC:HGNC:38034
            dbxref_vals = val.split(',')
            for e in dbxref_vals:
                arr = e.split(':')
                dbxref_param = arr[0].lower()
                dbxref_val = arr[1]
                if dbxref_param == 'geneid':
                    desc_obj['gene_id'] = dbxref_val
                elif dbxref_param == 'genbank':
                    desc_obj['genbank'] = dbxref_val
                elif dbxref_param == 'ensembl':
                    desc_obj['ensembl'] = dbxref_val
                else:
                    break
    
    return desc_obj

def _gff_parseline(line, regions):
    if line[0] == '#':
        return False
    else:
        words = line.split('\t')
        sequence_id = words[0]
        refseq = words[1]
        region = words[2]
        start = int(words[3]) # One-based numbering.
        start_index = start-1 # Zero-based numbering.
        end = int(words[4])
        end_index = end-1
        desc = words[8] # Description.
        desc_obj = _parse_desc(desc)
        gene = desc_obj['gene'] if 'gene' in desc_obj.keys() else '' # Gene name.
        gene_id = desc_obj['gene_id'] if 'gene_id' in desc_obj.keys() else '' # Gene ID
        genbank = desc_obj['genbank'] if 'genbank' in desc_obj.keys() else '' # GeneBank
        ensembl = desc_obj['ensembl'] if 'ensembl' in desc_obj.keys() else '' # Ensembl
        if regions is None:
            return {'sequence_id': sequence_id, 'refseq': refseq, 'region': region, 'start': start, 'start_index': start_index, 'end': end, 'end_index': end_index, 'desc': desc_obj, 'gene': gene, 'gene_id': gene_id, 'genbank': genbank, 'ensembl': ensembl}
        elif region in regions:
            return {'sequence_id': sequence_id, 'refseq': refseq, 'region': region, 'start': start, 'start_index': start_index, 'end': end, 'end_index': end_index, 'desc': desc_obj, 'gene': gene, 'gene_id': gene_id, 'genbank': genbank, 'ensembl': ensembl}
        else:
            return False

def gff_to_csv(file, csv_output, regions):
    if os.path.exists(file):
        # Prepare file and dataframe.
        if os.path.exists(csv_output):
            os.remove(csv_output)
        colnames = ['sequence_id', 'refseq', 'region', 'start_index', 'end_index', 'start', 'end', 'gene', 'gene_id', 'genebank', 'ensembl']
        header = ",".join(colnames)
        f = open(file, 'r')
        out = open(csv_output, 'x')
        out.write("{} \n".format(header))
        
        for line in f:
            d = _gff_parseline(line, regions)
            try:
                if d != False:
                    if d:
                        output = "{},{},{},{},{},{},{},{},{},{},{}\n".format(d['sequence_id'], d['refseq'], d['region'], d['start_index'], d['end_index'], d['start'], d['end'], d['gene'], d['gene_id'], d['genbank'], d['ensembl'])
                        out.write(output)
                    else:
                        break
            except:
                out.close()
                f.close()

        out.close()
        f.close()

print(genome_grch37)
print(genome_grch38)
print(grch37_sample_dir)
print(grch38_sample_dir)


./data/genome/grch37/GRCh37_latest_genomic.gff
./data/genome/grch38/GRCh38_latest_genomic.gff
./sample/grch37
./sample/grch38


In [52]:
# s = "NC_000001.11	RefSeq	region	1	248956422	.	+	.	ID=NC_000001.11:1..248956422;Dbxref=taxon:9606;Name=1;chromosome=1;gbkey=Src;genome=chromosome;mol_type=genomic DNA"
# s = "NC_000001.11	BestRefSeq	exon	13221	14409	.	+	.	ID=exon-NR_046018.2-3;Parent=rna-NR_046018.2;Dbxref=GeneID:100287102,Genbank:NR_046018.2,HGNC:HGNC:37102;gbkey=misc_RNA;gene=DDX11L1;product=DEAD/H-box helicase 11 like 1 (pseudogene);pseudo=true;transcript_id=NR_046018.2"
s = "NC_000001.11	BestRefSeq	exon	29321	29370	.	-	.	ID=exon-NR_024540.1-1;Parent=rna-NR_024540.1;Dbxref=GeneID:653635,Genbank:NR_024540.1,HGNC:HGNC:38034;gbkey=misc_RNA;gene=WASH7P;product=WASP family homolog 7%2C pseudogene;pseudo=true;transcript_id=NR_024540.1"
d = _gff_parseline(s, ['exon'])
d


{'sequence_id': 'NC_000001.11',
 'refseq': 'BestRefSeq',
 'region': 'exon',
 'start': 29321,
 'start_index': 29320,
 'end': 29370,
 'end_index': 29369,
 'desc': {'id': 'exon-NR_024540.1-1',
  'parent': 'rna-NR_024540.1',
  'dbxref': 'GeneID:653635,Genbank:NR_024540.1,HGNC:HGNC:38034',
  'gene_id': '653635',
  'genbank': 'NR_024540.1',
  'gbkey': 'misc_RNA',
  'gene': 'WASH7P',
  'product': 'WASP family homolog 7%2C pseudogene',
  'pseudo': 'true',
  'transcript_id': 'NR_024540.1'},
 'gene': 'WASH7P',
 'gene_id': '653635',
 'genbank': 'NR_024540.1',
 'ensembl': ''}

In [11]:
gff_to_csv(genome_grch37, grch37_sample_dir + "/grch37_all_07012022.csv", None)

In [73]:
gff_to_csv(genome_grch38, grch38_sample_dir + "/grch38_all.csv", None)

In [53]:
gff_to_csv(genome_grch37, grch37_sample_dir + "/grch37_exon_only_06012022.csv", ['exon'])

In [54]:
gff_to_csv(genome_grch38, grch38_sample_dir + "/grch38_exon_only_06012022.csv", ['exon'])

In [46]:
colnames = ['sequence_id', 'refseq', 'region', 'start_index', 'end_index', 'start', 'end', 'gene', 'gene_id', 'genbank', 'ensembl']
header = ",".join(colnames)
header

'sequence_id,refseq,region,start_index,end_index,start,end,gene,gene_id,genbank,ensembl'

In [56]:
def gff_to_csvs(gff_file, target_folder, regions, header):
    f = open(gff_file)
    target_file = target_folder + '/'
    cur_seq = ""
    temp_seq = ""
    output_file = ""
    file_to_write = {}
    for line in f:
        d = _gff_parseline(line, regions)
        if d:
            output = "{},{},{},{},{},{},{},{},{},{},{} \n".format(d['sequence_id'], d['refseq'], d['region'], d['start_index'], d['end_index'], d['start'], d['end'], d['gene'], d['gene_id'], d['genbank'], d['ensembl'])
            temp_seq = d['sequence_id']
            if cur_seq == "":
                cur_seq = temp_seq

            # Prepare desired file to write.
            output_file = target_file + temp_seq + '.csv'

            # Compare if this sequence_id is the as previous sequence_id.
            if temp_seq == cur_seq:

                # If it is then write to desired file.
                # Check if file exists. If not then create file.
                if os.path.exists(output_file):
                    file_to_write.write(output)
                else:
                    file_to_write = open(output_file, 'x')

                    # Write header first.
                    file_to_write.write("{}\n".format(header))
                    file_to_write.write(output)
            
            # If this sequence_id is not the same as previous sequence_id, close the existing file.
            elif cur_seq != temp_seq:
                file_to_write.close()
                cur_seq = temp_seq

    # Close any file related to this procedure.
    file_to_write.close()
    f.close()                


In [74]:
gff_to_csvs(genome_grch38, './sample/grch38/genes', None, header)


In [57]:
gff_to_csvs(genome_grch37, './sample/grch37/genes', None, header)

In [75]:
from Bio import SeqIO
from data_dir import hs_nc1

print(hs_nc1)

./data/homo-sapiens/NC_000001.11.fasta


In [78]:
"""
    complete_sequence_file  : path of complete sequence file in FASTA format.
    label_location_file     : path of file containing exon region in CSV.
"""
def generate_labels(complete_sequence_file):
    print("reading complete sequence at {} \n".format(complete_sequence_file))
    seq = SeqIO.parse(complete_sequence_file, "fasta")
    return seq

seq = generate_labels(hs_nc1)
complete_sequence = list(seq)[0].seq
complete_labels = ['.' if a != 'N' else 'N' for a in complete_sequence]

reading complete sequence at ./data/homo-sapiens/NC_000001.11.fasta 



In [76]:
from data_dir import chr1
print(chr1)

ImportError: cannot import name 'chr1' from 'data_dir' (c:\Workspace\research\sequence-processing\data_dir.py)

In [82]:
"""
Char 'N' represents any base. It indicates that sequence has no information regarding the base at that position.
Char '.' represents any feature other than Exon. Char 'E' is exon.
"""
# Try open the csv using pandas.
import pandas as pd

df = pd.read_csv('./sample/grch38/genes/NC_000001.11.csv')
df.head(3)
df[df['region'] == 'region'].loc[0]['end_index']

248956421

In [141]:
# Get all gene in dataframe.
genes = df['gene'].unique()
genes = list(genes)
genes = [a for a in genes if str(a) != 'nan']
print('how many gene? {}'.format(len(genes)))
# print(genes)
genes[0]
ndf = df[df['gene'] == genes[0]]
#ndf = ndf.loc[ndf['region'].isin(['gene', 'pseudogene'])]
ndf.iloc[0]['region']
ndf = ndf[ndf['region'] == 'exon']
ndf

how many gene? 5094


sequence_id      refseq region  start_index  end_index  start    end  \
3  NC_000001.11  BestRefSeq   exon        11873      12226  11874  12227   
4  NC_000001.11  BestRefSeq   exon        12612      12720  12613  12721   
5  NC_000001.11  BestRefSeq   exon        13220      14408  13221  14409   

      gene      gene_id      genbank ensembl  
3  DDX11L1  100287102.0  NR_046018.2          
4  DDX11L1  100287102.0  NR_046018.2          
5  DDX11L1  100287102.0  NR_046018.2

In [151]:
for g in genes:
    # Filter dataframe to contain certain genbank.
    ndf = df[df['gene'] == g]

    g_region_df = ndf.loc[ndf['region'].isin(['gene', 'pseudogene'])]
    g_start_index = g_region_df.iloc[0]['start_index']
    g_end_index = g_region_df.iloc[0]['end_index']

    # Prepare sequence and its label.
    g_sequence = complete_sequence[g_start_index:g_end_index+1]
    g_label = ['N' if a == 'N' else '.' for a in g_sequence]

    # Generate labels from this dataframe.
    try:
        exons = ndf[ndf['region'] == 'exon']
        for i, row in exons.iterrows():
            s = row['start_index']
            e = row['end_index']

            for j in range(s, e+1):
                rel_index = j-g_start_index
                g_label[rel_index] = 'E' if g_label[rel_index] != 'N' else 'N'

        fname = fname = './sample/grch38/labels/{}.txt'.format(g)
        g_file = open(fname, 'x')
        g_file.write('{}\n{}\n'.format(g_sequence, "".join(g_label)))
        g_file.close()
    except IndexError:
        print('gene {}, length {}'.format(g, len(g_sequence)))
        print('gene region {}-{}'.format(g_start_index, g_end_index))




exon at 11873-12226
exon at 12612-12720
exon at 13220-14408
exon at 29320-29369
exon at 24737-24890
exon at 18267-18365
exon at 17914-18060
exon at 17605-17741
exon at 17232-17367
exon at 16857-17054
exon at 16606-16764
exon at 15795-15946
exon at 14969-15037
exon at 14361-14828
exon at 17368-17435
exon at 17368-17390
exon at 17408-17430
exon at 29925-30038
exon at 30563-30666
exon at 30975-31294
exon at 30365-30502
exon at 30437-30457
exon at 35720-36080
exon at 35276-35480
exon at 34610-35173
exon at 65418-65432
exon at 65519-65572
exon at 69036-71584
exon at 267302-267353
exon at 112699-112803
exon at 92090-92239
exon at 89005-91628
exon at 173752-174658
exon at 172556-172687
exon at 169048-169263
exon at 167958-168164
exon at 165883-165941
exon at 92090-92239
exon at 89005-91628
exon at 173752-174413
exon at 172556-172687
exon at 169048-169263
exon at 168099-168164
exon at 165883-165941
exon at 92090-92239
exon at 89005-91628
exon at 167963-168092
exon at 165883-165941
exon at 9209

In [67]:
label_seq1 = [c for c in complete_labels]

for i, row in df.iterrows():
    start_index = row['start_index']
    end_index = row['end_index']
    # print("region {}-{}".format(start_index, end_index))
    for j in range(start_index, end_index+1):
        label_seq1[j] = 'E'

In [68]:
def split_string(s, length):
    return (s[0+i:length+i] for i in range(0, len(s), length))

arr_label = split_string(label_seq1, 50)
f = open('chr1.label.txt', 'x')
for label in arr_label:
    f.write("{}\n".format("".join(label)))
f.close()